In [1]:
from deeppavlov.models.spelling_correction.levenshtein.searcher_component import LevenshteinSearcherComponent
import numpy as np
DATA_PATH = "/home/alx/Cloud/spell_corr/py_spelling_corrector/data/"


[nltk_data] Downloading package punkt to /home/alx/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /home/alx/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package perluniprops to /home/alx/nltk_data...
[nltk_data]   Package perluniprops is already up-to-date!
[nltk_data] Downloading package nonbreaking_prefixes to
[nltk_data]     /home/alx/nltk_data...
[nltk_data]   Package nonbreaking_prefixes is already up-to-date!


In [2]:
# Copyright 2017 Neural Networks and Deep Learning lab, MIPT
#
# Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
#     http://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

from pathlib import Path
from typing import List, Tuple

import kenlm

from deeppavlov.core.commands.utils import expand_path
from deeppavlov.core.common.registry import register
from deeppavlov.core.models.component import Component
from deeppavlov.core.common.log import get_logger


class KenlmElector(Component):
    """Component that chooses a candidate with the highest product of base and language model probabilities

    Args:
         load_path: path to the kenlm model file
         beam_size: beam size for highest probability search

    Attributes:
        lm: kenlm object
        beam_size: beam size for highest probability search
    """
    def __init__(self, load_path: Path, beam_size: int=4, *args, **kwargs):
        self.lm = kenlm.Model(str(expand_path(load_path)))
        self.beam_size = beam_size

    def __call__(self, batch: List[List[List[Tuple[float, str]]]]) -> List[List[str]]:
        """Choose the best candidate for every token

        Args:
            batch: batch of probabilities and string values of candidates for every token in a sentence.
            Ex.:
            [
                [
                    [
                        (-0.0, 'все'),(-4.0, 'вес'), (-4.0, 'вс'), (-4.0, 'всг'),(-4.0, 'вси'),
                        (-4.0, 'вск'),(-4.0, 'всл'),(-4.0, 'овсе')],
                    [
                        (-0.0, 'смешалось'),(-4.0, 'смешало ь'),(-4.0, 'мешалось'),
                        (-4.0, 'вмешалось'),(-4.0, 'с мешалось')],
                    [
                        (-0.0, 'кони'),(-4.0, 'кон'),(-4.0, 'кона'),(-4.0, 'конв'),
                        (-4.0, 'коне'),(-4.0, 'конн'),(-4.0, 'коно'),(-4.0, 'клони')],
                    [
                        (-0.0, 'люди'),(-4.0, 'люд'),(-4.0, 'леди'),(-4.0, 'лю ди'),
                        (-4.0, 'блюди')]
                ]
            ]

        Returns:
            batch of corrected tokenized sentences
        """
        return [self._infer_instance(candidates) for candidates in batch]

    def _infer_instance(self, candidates: List[List[Tuple[float, str]]]):
        candidates = candidates + [[(0, '</s>')]]
        state = kenlm.State()
        self.lm.BeginSentenceWrite(state)
        beam = [(0, state, [])]
        for sublist in candidates:
            new_beam = []
            for beam_score, beam_state, beam_words in beam:
                for score, candidate in sublist:
                    prev_state = beam_state
                    c_score = 0
                    cs = candidate.split()
                    for candidate in cs:
                        state = kenlm.State()
                        c_score += self.lm.BaseScore(prev_state, candidate, state)
                        prev_state = state
                    new_beam.append((beam_score + score + c_score, state, beam_words + cs))
            new_beam.sort(reverse=True)
            beam = new_beam[:self.beam_size]
        score, state, words = beam[0]
        return words[:-1]
    
    ##########################################################################
    def _tokenize(self, sentence):
        return sentence.split()
    
    def estimate_pure_likelihood(self, sentence):
        """Given a sentence it estimates its likelihood without spelling correction fixes"""
        return self.lm.score(sentence)        
    
    def score_sentences(self, sentences):
        """
        Scores batch of sentences
        """
        return [self.lm.score(sentence) for sentence in sentences]
    
    def estimate_likelihood_with_correction_scores(self, tokenized_sentence_with_correction_scores):
        """Given a sentence it estimates its likelihood with spelling correction fixes"""
        #TODO
        
    def score_sentences_hypotheses(self, hypotheses):
        candidates = candidates + [[(0, '</s>')]]
        state = kenlm.State()
        self.lm.BeginSentenceWrite(state)
        beam = [(0, state, [])]
        for sublist in candidates:
            new_beam = []
            for beam_score, beam_state, beam_words in beam:
                for score, candidate in sublist:
                    prev_state = beam_state
                    c_score = 0
                    cs = candidate.split()
                    for candidate in cs:
                        state = kenlm.State()
                        c_score += self.lm.BaseScore(prev_state, candidate, state)
                        prev_state = state
                    new_beam.append((beam_score + score + c_score, state, beam_words + cs))
            new_beam.sort(reverse=True)
            beam = new_beam[:self.beam_size]
        score, state, words = beam[0]
        return words[:-1]
        

In [3]:
from copy import copy, deepcopy

class LanguageModel():
    def tokenize(self, sent_str):
        pass

    def estimate_likelihood(self, sent_str):
        pass

    def score_sentences(self, sentences):
        return np.random.rand(len(sentences))

class TokenHypothesis():
    def __init__(self, text, err_score=0.0):
        self.text = text
#         self.lm_score = 0
        # score for error:
        self.err_score = err_score
        # counter which helps to estimate how many words was merged
        # this is used to multiply likelihood of unknown word
        self.merges_count = 0
        
    def merge_with_suffix(self, suffix_str, err_score):
        self.text += suffix_str
        self.err_score += err_score
        self.merges_count+=1
        return self
    
class SentenceHypothesis():
    def __init__(self, text):
        self.text = text
#         self.score = np.nan
        self.lm_score = 0
        # score for error:
#         self.err_score = err_score
        
        # token hypotheses of the sentence
        self.token_hypotheses = []
        
    def total_score(self):
        return self.lm_score+self.err_score()
    
    def err_score(self):
        # calculates error score from token errors
        total_error = 0
        for each_tok_hyp in self.token_hypotheses:
            total_error+=each_tok_hyp.err_score
        return total_error
    
    def fork_for_each_suffix(self, suffixes, error_scores=None):
        """Given a list of suffixes strings it forks the current hypotheses into several
        hypotheses for each suffix

        : param error_scores: score for suffix, usually negative value (logit score), suffix error score is incremented to
        baseline hypothesis score
        """
        hypotheses_list = []
        #         import ipdb; ipdb.set_trace()
        for idx, each_suffix in enumerate(suffixes):
            new_sentence_hypothesis = deepcopy(self)
            new_sentence_hypothesis.text += each_suffix

            if each_suffix[0] == " ":
                # new token case
                # if suffix starts with space character, then we have a token split
                tok_hypothesis = TokenHypothesis(each_suffix[1:], error_scores[idx])
                new_sentence_hypothesis.token_hypotheses.append(tok_hypothesis)

            else:
                # continuation case hypothesis
                tokens_count = len(new_sentence_hypothesis.token_hypotheses)
                if tokens_count == 0:
                    # the first token in sentence case
                    tok_hypothesis = TokenHypothesis(each_suffix, error_scores[idx])
                    new_sentence_hypothesis.token_hypotheses.append(tok_hypothesis)

                else:
                    # get last token and merge it with suffix:

                    last_token_hypothesis = new_sentence_hypothesis.token_hypotheses[
                        tokens_count - 1]
                    last_token_hypothesis = deepcopy(last_token_hypothesis)
                    last_token_hypothesis.merge_with_suffix(each_suffix[1:], error_scores[idx])
                    # substitute the last token hypothesis with enlarged one
                    new_sentence_hypothesis.token_hypotheses[
                        tokens_count - 1] = last_token_hypothesis

            hypotheses_list.append(new_sentence_hypothesis)

        return hypotheses_list
#     def fork_for_each_suffix(self, suffixes, error_scores=None):
#         """Given a list of suffixes strings it forks the current hypotheses into several
#         hypotheses for each suffix
        
#         : param error_scores: score for suffix, usually negative value (logit score), suffix error score is incremented to 
#         baseline hypothesis score
#         """
#         hypotheses_list = []
# #         import ipdb; ipdb.set_trace()
#         for idx, each_suffix in enumerate(suffixes):
#             new_sentence_hypothesis = copy(self)
#             new_sentence_hypothesis.text += each_suffix
            
#             if each_suffix[0]==" ":
#                 # new token case
#                 # if suffix starts with space character, then we have a token split                
#                 tok_hypothesis = TokenHypothesis(each_suffix[1:], error_scores[idx])
#                 new_sentence_hypothesis.token_hypotheses.append(tok_hypothesis)
                
#             else:
#                 # continuation case hypothesis
#                 tokens_count = len(new_sentence_hypothesis.token_hypotheses)
#                 if tokens_count==0:
#                     # the first token in sentence case
#                     tok_hypothesis = TokenHypothesis(each_suffix, error_scores[idx])
#                     new_sentence_hypothesis.token_hypotheses.append(tok_hypothesis)
                    
#                 else:
#                     # get last token and merge it with suffix:
                    
#                     last_token_hypothesis = new_sentence_hypothesis.token_hypotheses[tokens_count-1]
#                     last_token_hypothesis = copy(last_token_hypothesis)
#                     last_token_hypothesis.merge_with_suffix(each_suffix[1:], error_scores[idx])
#                     # substitute the last token hypothesis with enlarged one
#                     new_sentence_hypothesis.token_hypotheses[tokens_count-1]=last_token_hypothesis
                    
#             hypotheses_list.append(new_sentence_hypothesis)

#         return hypotheses_list   
    
    def __repr__(self):        
        out_text = " score: %f" % self.total_score()        
        text = "hypothesis: %s" % self.text
        return text + out_text
    
class HypothesesHub():
    def __init__(self):
        # init with null hypothesis:
        self.hypotheses = [SentenceHypothesis("")]
        
        # dummy LM:
#         self.lm = LanguageModel()
        
#         # KenLM Elector as LM:
#         ROOT_PATH = "~/.deeppavlov"
#         DOWNLOADS_PATH = ROOT_PATH + "/downloads"        
#         self.lm = KenlmElector(load_path=DOWNLOADS_PATH+"/language_models/ru_wiyalen_no_punkt.arpa.binary")
        
        self.max_score = 0.0

    def get_scores(self):
        """Returns summarized scores Error + LM score"""
        scores = [each_hypo.total_score() for each_hypo in self.hypotheses]
        return scores

    def append_partial_hypotheses(self, partial_candidates, error_scores=None):
        """
        For each hypothesis in the hub it appends all candidates
        :param partial_candidates:
        :return: updated self
        """
        new_hypotheses = []
        if self.hypotheses:
            for each_hypothesis in self.hypotheses:
                hypos = each_hypothesis.fork_for_each_suffix(partial_candidates, error_scores=error_scores)
                new_hypotheses += hypos
        else:
            print("No hypotheses!!!!")
        self.hypotheses = new_hypotheses
        return self

#     def score_hypotheses(self):
#         """
#         Command to run scoring of all hypotheses by language model scoring function
#         :return: list of scored hypotheses
#         """
        
#         sentences = [each_hypo.text for each_hypo in self.hypotheses]
#         scores = self.lm.score_sentences(sentences)

#         for num, each_hypo in enumerate(self.hypotheses):
#             each_hypo.lm_score = scores[num]
#         return self.hypotheses

    def prune_low_prob_hypotheses(self, prob_pruning_treshold=None, max_number_of_hypotheses=200):
        """
        Prunes hypotheses that has probability lower than treshold value.
        treshold value depends on value of max prob hypothesis.

        :param prob_pruning_treshold: [0,1] ratio of max probability that is required for a
        hypothesis to be kept in hypotheses hub
        :return:
        """
        scores = self.get_scores()
        # number check
        filtered_hypotheses = sorted(self.hypotheses, key=lambda x: x.total_score(), reverse=True)        
        if len(self.hypotheses)>max_number_of_hypotheses:
            # prune those which are the worst
            self.hypotheses = filtered_hypotheses[:max_number_of_hypotheses]     
            
        return self.hypotheses


class SpellingCorrectionCandidatesGenerator():
    """
    Generates candidates for words (words) with error scores
    """
    # decrement for frequent errors
    FREQUENT_ERRORS_DECREMENT_SCORE = -4.0
    EXCESSIVE_SPACE_ERROR_DECREMENT_SCORE = -6.0
    
    def __init__(self, path_to_dictionary=None):

        words_dict = []
        if not path_to_dictionary:
            path_to_dictionary = DATA_PATH + "compreno_wordforms.txt"
#             path_to_dictionary = DATA_PATH + "russian_words_vocab.dict"
        
        with open(path_to_dictionary, "r") as dict_file:
            words_dict = dict_file.read().splitlines()
        self.lsc = LevenshteinSearcherComponent(words=words_dict)

    def gen_candidates(self, token):
        """
        Given a token string generates candidates with error scores
        :param token: string with token
        :return:
        """
        #TODO black list support: some tokens should not variate (SB requirement)
        scored_candidates=self.lsc([[token]])[0][0]
        scores, w_forms = zip(*scored_candidates)
        w_forms = list(w_forms)
        scores = list(scores)
        # ############################################################################################
        # here is rule based/statistical substitutions with distant levenshtein can be applied:
                
        if token == "нить":
            w_forms.append("нибудь")
            scores.append(self.FREQUENT_ERRORS_DECREMENT_SCORE)
        elif token in ["оч"]:
            w_forms.append("очень")
            scores.append(self.FREQUENT_ERRORS_DECREMENT_SCORE)
        elif token in ["што", "шо", "чо", "чё"]:
            w_forms.append("что")
            scores.append(self.FREQUENT_ERRORS_DECREMENT_SCORE)
        elif token in ["ваще", "воще"]:
            w_forms.append("вообще")
            scores.append(self.FREQUENT_ERRORS_DECREMENT_SCORE)
        elif token in ["вообщем"]:
            w_forms.append("в общем")
            scores.append(self.FREQUENT_ERRORS_DECREMENT_SCORE)
        elif token in ["писят"]:
            w_forms.append("пятьдесят")
            scores.append(self.FREQUENT_ERRORS_DECREMENT_SCORE)
        elif token in ["аццкий"]:
            w_forms.append("адский")
            scores.append(self.FREQUENT_ERRORS_DECREMENT_SCORE)
        elif token in ["помойму", "помоиму"]:
            w_forms.append("по-моему")
            scores.append(self.FREQUENT_ERRORS_DECREMENT_SCORE)

        return scores, w_forms

    def variate_with_prefixes(self, candidates, error_scores):
        """
        Given a tokens candidates this method enriches the space of candidates with prefixed variants
        by default it prepends prefixes of the space and hyphen to tokens.

        So ["то"] -> ["то", "-то", " то"]

        :param candidates: list of candidate strings
        :param prefixes: list of possible prefixes
        :return: list of candidates enriched with prefixed versions
        """
        
#         prefixes = [" ", "-"]
        result_candidates = []
        result_scores = []
        for idx, each_candidate in enumerate(candidates):
            # add candidate produced by erroneous space problem.
            # Ex.: "при вет" -> "привет":
            result_candidates.append(each_candidate)
            result_scores.append(error_scores[idx] + self.EXCESSIVE_SPACE_ERROR_DECREMENT_SCORE)
            
            # add space candidate (no fix)
            result_candidates.append(" " + each_candidate)
            result_scores.append(error_scores[idx] + 0.0)
            
            # add hyphen candidates conditionally:
            # TODO improve heuristics for hyphen adding?
            # TODO add hyphen after "по"
            if each_candidate in ["то", "таки", "нибудь", "моему", "нашему", "твоему", "любому", "за", "другому", "как",
                                 "русски", "разному"]:
                result_candidates.append("-" + each_candidate)
                result_scores.append(error_scores[idx] + self.FREQUENT_ERRORS_DECREMENT_SCORE)
#         print("result_scores, result_candidates")
#         print(result_scores, result_candidates)
        return result_scores, result_candidates
    
class SpellingCorrector():
    # language_model;
    # error model;
    def __init__(self, sccg=None, language_model=None):
        """
        sccg - spelling corrector hypotheses generator instance
        lang_model - language model instance, by default KenLM
        """
        
        # setup hypotheses generator:
        if not sccg:
            self.sccg = SpellingCorrectionCandidatesGenerator()
        else:
            self.sccg = sccg
        
        # setup language model:
        if not language_model:
            # KenLM Elector as LM:
            ROOT_PATH = "~/.deeppavlov"
            DOWNLOADS_PATH = ROOT_PATH + "/downloads"        
            self.lm = KenlmElector(load_path=DOWNLOADS_PATH+"/language_models/ru_wiyalen_no_punkt.arpa.binary")

        else:
            self.lm = language_model
    
    def score_hypothesis(self, sentence_hypothesis):
        state = kenlm.State()
        self.lm.lm.BeginSentenceWrite(state)
        beam = [(0, state, [])]
        for each_tok_hypothesis in sentence_hypothesis.token_hypotheses:
            err_score = each_tok_hypothesis.err_score
            merges_count = each_tok_hypothesis.merges_count
            prev_state = state
            c_score = 0
            cs = each_tok_hypothesis.text.split()
            for candidate in cs:            
                state = kenlm.State()            
                c_score += self.lm.BaseScore(prev_state, candidate, state)
                prev_state = state
                
                new_beam.append((beam_score + score + c_score, state, beam_words + cs))
#             new_beam = []
#             for beam_score, beam_state, beam_words in beam:
                
            new_beam.sort(reverse=True)
            beam = new_beam[:self.beam_size]
        score, state, words = beam[0]
        return words[:-1]
        
            
            
    def score_hypotheses_hub(self, hypotheses_hub):
        """Score hypotheses by LM
        Command to run scoring of all hypotheses by language model scoring function
        :return: list of scored hypotheses
        
        """
        
        sentences = [each_hypo.text for each_hypo in hypotheses_hub.hypotheses]
        scores = self.lm.score_sentences(sentences)

        for num, each_hypo in enumerate(hypotheses_hub.hypotheses):
            each_hypo.lm_score = scores[num]
        return hypotheses_hub.hypotheses
        
        
#         return hypotheses_hub.score_hypotheses()
    
    def analyze_sentence(self, sentence):
        """
        Method for analyzing sentence: generating hypotheses and scoring them
        
        :param sentence: str, sentence with errors
        :return: correction hypotheses of the sentence
        """
        self.hypo_hub = HypothesesHub()
        # preprocessing:
        # TODO make lowercasing revertible:
        sentence = self.lowercase(sentence)        
        tokenized_input = self._tokenize(sentence)
#         import ipdb; ipdb.set_trace()
        for idx, each_tok in enumerate(tokenized_input):
            # TODO optionally you could pass left and right context
            err_scores, tok_candidates = self.sccg.gen_candidates(each_tok)
            if idx>0:
                # TODO optionally you could pass left and right context
                err_scores, tok_candidates = self.sccg.variate_with_prefixes(tok_candidates, err_scores)
            print(tok_candidates)
            self.hypo_hub = self.hypo_hub.append_partial_hypotheses(tok_candidates, err_scores)
            
            self.score_hypotheses_hub(self.hypo_hub)
            self.hypo_hub.prune_low_prob_hypotheses()
            
        return self.hypo_hub.hypotheses
    
    def __call__(self, input_sentences_batch):
        """
        Given a batch of sentences it returns a batch of corrected sentences
        """
        outputs = []
        for each_sent in input_sentences_batch:
            hypotheses = self.analyze_sentence(each_sent)
            the_best_hypothesis = hypotheses[0]
            outputs.append(the_best_hypothesis.text)
        return outputs
    
    def lowercase(self, sent_str):
        return sent_str.lower()
    
    def _tokenize(self, sent_str):
        return sent_str.split()

    def predict_correct(self, sentence_str):
        """
        predicts correction of the sentence
        :param sentence_str:
        :return:
        """

        pass

In [4]:
# init it once because it loads for 2.5 minutes:
sccg = SpellingCorrectionCandidatesGenerator()

In [5]:
sc = SpellingCorrector(sccg=sccg)

In [6]:
hypotheses = sc.analyze_sentence("привет помпушка")
hypotheses

['привет', 'привез', 'привей', 'привел', 'привес', 'привета', 'привете', 'привето', 'привету', 'приветы', 'приветь', 'приват', 'привит', 'придет', 'прилет', 'примет', 'причет', 'при ет', 'приврет', 'привьет', 'пр вет', 'при вет', 'п ивет', 'пр ивет']
['помпу ка', ' помпу ка', 'пом ушка', ' пом ушка', 'помп ушка', ' помп ушка', 'попушка', ' попушка', 'подпушка', ' подпушка', 'по пушка', ' по пушка', 'пом пушка', ' пом пушка', 'пампушка', ' пампушка', 'помпушка', ' помпушка']


[hypothesis: привет пампушка score: -21.205189,
 hypothesis: приветпопушка score: -21.274544,
 hypothesis: приветподпушка score: -21.274544,
 hypothesis: приветпампушка score: -21.274544,
 hypothesis: привет подпушка score: -21.391972,
 hypothesis: привет попушка score: -21.419556,
 hypothesis: привет по пушка score: -21.748955,
 hypothesis: привел пампушка score: -24.174213,
 hypothesis: примет пампушка score: -24.283638,
 hypothesis: привел подпушка score: -24.361000,
 hypothesis: привел попушка score: -24.388582,
 hypothesis: примет подпушка score: -24.470421,
 hypothesis: придет по пушка score: -24.471622,
 hypothesis: примет попушка score: -24.498005,
 hypothesis: придет пампушка score: -24.575901,
 hypothesis: привез пампушка score: -24.609825,
 hypothesis: привел по пушка score: -24.715149,
 hypothesis: примет по пушка score: -24.752254,
 hypothesis: придет подпушка score: -24.762684,
 hypothesis: придет попушка score: -24.790268,
 hypothesis: привез подпушка score: -24.796612,


In [7]:
hypotheses[0].err_score()

-4.0

In [36]:
hypotheses[0].token_hypotheses[0].text

'приветривезривейривелривесриветариветериветориветуриветыриветьриватривитридетрилетриметричетри етривретривьетр ветри вет иветр иветомпу ка'

In [9]:
sc(["привет помпушка"])

['']

In [ ]:
# evaluate model

In [8]:
DIALOG_DATA_PATH = 'data/dialog/'
# Train data
TRAIN_ERRONEOUS_DATA = DIALOG_DATA_PATH + "source_sents.txt"
TRAIN_GOLDEN_DATA = DIALOG_DATA_PATH + "corrected_sents.txt"

# Test data
TEST_ERRONEOUS_DATA = DIALOG_DATA_PATH + "test_sample_testset.txt"
TEST_GOLDEN_DATA = DIALOG_DATA_PATH + "corr_sample_testset.txt"

In [9]:
with open(TEST_ERRONEOUS_DATA, 'r') as sents_file:
    erroneous_lines = sents_file.readlines()
    erroneous_lines = [line.strip() for line in erroneous_lines]
    
with open(TEST_GOLDEN_DATA, 'r') as sents_file:
    golden_lines = sents_file.readlines()
    golden_lines = [line.strip() for line in golden_lines]

In [10]:
from evaluate import evaluate_spelling_corrector
import datetime as dt

In [ ]:
start_dt = dt.datetime.now()
hypotheses = sc(erroneous_lines)
fin_dt = dt.datetime.now()
print(fin_dt-start_dt)

['\ufeffесть']
['у', ' у', '$', ' $', '%', ' %', '?', ' ?', '£', ' £', '§', ' §', '°', ' °', 'а', ' а', 'б', ' б', 'в', ' в', 'г', ' г', 'д', ' д', 'е', ' е', 'ж', ' ж', 'и', ' и', 'й', ' й', 'к', ' к', 'л', ' л', 'м', ' м', 'о', ' о', 'п', ' п', 'р', ' р', 'с', ' с', 'т', ' т', 'х', ' х', 'ц', ' ц', 'ч', ' ч', 'ш', ' ш', 'ь', ' ь', 'ю', ' ю', 'я', ' я', 'у.', ' у.', 'уб', ' уб', 'уд', ' уд', 'уж', ' уж', 'уз', ' уз', 'ук', ' ук', 'ул', ' ул', 'ум', ' ум', 'ун', ' ун', 'ур', ' ур', 'ус', ' ус', 'уф', ' уф', 'ух', ' ух', 'ую', ' ую', 'бу', ' бу', 'ву', ' ву', 'гу', ' гу', 'ду', ' ду', 'зу', ' зу', 'йу', ' йу', 'ку', ' ку', 'лу', ' лу', 'му', ' му', 'ну', ' ну', 'оу', ' оу', 'пу', ' пу', 'ру', ' ру', 'су', ' су', 'ту', ' ту', 'фу', ' фу', 'ху', ' ху', 'чу', ' чу', 'шу', ' шу']
['вас', ' вас', 'ва', ' ва', 'ваг', ' ваг', 'вад', ' вад', 'важ', ' важ', 'ваз', ' ваз', 'вай', ' вай', 'вак', ' вак', 'вал', ' вал', 'вам', ' вам', 'ван', ' ван', 'вар', ' вар', 'ват', ' ват', 'вау', ' вау', 'вах'

['всю', ' всю', 'вс', ' вс', 'все', ' все', 'вся', ' вся', 'вею', ' вею', 'вию', ' вию', 'вою', ' вою', 'выю', ' выю', 'вью', ' вью', 'вэю', ' вэю', 'в ю', ' в ю', 'всею', ' всею', 'всую', ' всую', 'вс ю', ' вс ю', 'сю', ' сю', 'асю', ' асю', 'ксю', ' ксю', 'осю', ' осю', 'хсю', ' хсю', 'ясю', ' ясю', 'васю', ' васю', 'в сю', ' в сю']
['жизнь', ' жизнь', 'жизне', ' жизне', 'жизни', ' жизни', 'жизнью', ' жизнью']
['запомню', ' запомню', 'запомни', ' запомни', 'заполню', ' заполню', 'за помню', ' за помню', 'напомню', ' напомню']
['свое', ' свое', 'свод', ' свод', 'своз', ' своз', 'свои', ' свои', 'свой', ' свой', 'свок', ' свок', 'свон', ' свон', 'своп', ' своп', 'свор', ' свор', 'свою', ' свою', 'своя', ' своя', 'своей', ' своей', 'своем', ' своем', 'своею', ' своею', 'сове', ' сове', 'свае', ' свае', 'св е', ' св е', 'своде', ' своде', 'свозе', ' свозе', 'своке', ' своке', 'своне', ' своне', 'свопе', ' свопе', 'своре', ' своре', 'сое', ' сое', 'сбое', ' сбое', 'сдое', ' сдое', 'слое',

['самых', ' самых', 'самы', ' самы', 'самые', ' самые', 'самый', ' самый', 'самым', ' самым', 'самах', ' самах', 'самих', ' самих', 'самох', ' самох', 'сам х', ' сам х', 'самы х', ' самы х', 'сам ых', ' сам ых']
['значимых', ' значимых', 'значимы', ' значимы', 'значимые', ' значимые', 'значимый', ' значимый', 'значимым', ' значимым', 'значим х', ' значим х', 'значимы х', ' значимы х', 'значим ых', ' значим ых']
['событий', ' событий', 'событие', ' событие', 'событии', ' событии', 'событию', ' событию', 'события', ' события', 'собы ий', ' собы ий']
['в', ' в', '$', ' $', '%', ' %', '?', ' ?', '£', ' £', '§', ' §', '°', ' °', 'а', ' а', 'б', ' б', 'г', ' г', 'д', ' д', 'е', ' е', 'ж', ' ж', 'и', ' и', 'й', ' й', 'к', ' к', 'л', ' л', 'м', ' м', 'о', ' о', 'п', ' п', 'р', ' р', 'с', ' с', 'т', ' т', 'у', ' у', 'х', ' х', 'ц', ' ц', 'ч', ' ч', 'ш', ' ш', 'ь', ' ь', 'ю', ' ю', 'я', ' я', 'в.', ' в.', 'ва', ' ва', 'вб', ' вб', 'ве', ' ве', 'ви', ' ви', 'во', ' во', 'вс', ' вс', 'вт', ' вт', 

['вот', ' вот', 'вто', ' вто', 'во', ' во', 'вов', ' вов', 'вод', ' вод', 'вое', ' вое', 'воз', ' воз', 'вой', ' вой', 'вок', ' вок', 'вол', ' вол', 'вон', ' вон', 'вор', ' вор', 'вос', ' вос', 'вою', ' вою', 'воя', ' воя', 'вота', ' вота', 'воте', ' воте', 'вотс', ' вотс', 'воту', ' воту', 'воты', ' воты', 'вт', ' вт', 'ват', ' ват', 'вет', ' вет', 'вит', ' вит', 'в т', ' в т', 'вогт', ' вогт', 'воет', ' воет', 'войт', ' войт', 'ворт', ' ворт', 'воют', ' воют', 'во т', ' во т', 'от', ' от', 'бот', ' бот', 'гот', ' гот', 'дот', ' дот', 'йот', ' йот', 'кот', ' кот', 'лот', ' лот', 'мот', ' мот', 'нот', ' нот', 'пот', ' пот', 'рот', ' рот', 'сот', ' сот', 'тот', ' тот', 'уот', ' уот', 'фот', ' фот', 'хот', ' хот', 'шот', ' шот', 'в от', ' в от', 'квот', ' квот', 'рвот', ' рвот']
['если', ' если', 'ес и', ' ес и', 'сели', ' сели', 'ели', ' ели', 'ебли', ' ебли', 'ерли', ' ерли', 'е ли', ' е ли', 'ес ли', ' ес ли', 'исли', ' исли', 'ясли', ' ясли', 'весли', ' весли', 'лесли', ' лесли', 'не

['этой', ' этой', 'это', ' это', 'этол', ' этол', 'этом', ' этом', 'этот', ' этот', 'этою', ' этою', 'это й', ' это й', 'эвой', ' эвой', 'экой', ' экой', 'элой', ' элой', 'эмой', ' эмой', 'эрой', ' эрой', 'эфой', ' эфой', 'этной', ' этной', 'эттой', ' эттой', 'той', ' той', 'атой', ' атой', 'отой', ' отой', 'стой', ' стой', 'ютой', ' ютой', 'бэтой', ' бэтой', 'тэтой', ' тэтой']
['лодке', ' лодке', 'лодка', ' лодка', 'лодки', ' лодки', 'лодко', ' лодко', 'лодку', ' лодку', 'лоде', ' лоде', 'лодае', ' лодае', 'лодже', ' лодже', 'лодзе', ' лодзе', 'лод е', ' лод е', 'локе', ' локе', 'лобке', ' лобке', 'лоеке', ' лоеке', 'ложке', ' ложке', 'локке', ' локке', 'лолке', ' лолке', 'ломке', ' ломке', 'лорке', ' лорке', 'лоске', ' лоске', 'лотке', ' лотке', 'ладке', ' ладке', 'ледке', ' ледке', 'лидке', ' лидке', 'людке', ' людке', 'водке', ' водке', 'годке', ' годке', 'ходке', ' ходке']
['большие', ' большие', 'больший', ' больший', 'большим', ' большим', 'большин', ' большин', 'больших', ' бол

...

['осознавать', ' осознавать', 'осозновать', ' осозновать']
['я', ' я', '$', ' $', '%', ' %', '?', ' ?', '£', ' £', '§', ' §', '°', ' °', 'а', ' а', 'б', ' б', 'в', ' в', 'г', ' г', 'д', ' д', 'е', ' е', 'ж', ' ж', 'и', ' и', 'й', ' й', 'к', ' к', 'л', ' л', 'м', ' м', 'о', ' о', 'п', ' п', 'р', ' р', 'с', ' с', 'т', ' т', 'у', ' у', 'х', ' х', 'ц', ' ц', 'ч', ' ч', 'ш', ' ш', 'ь', ' ь', 'ю', ' ю', 'яг', ' яг', 'яд', ' яд', 'як', ' як', 'ял', ' ял', 'ям', ' ям', 'ян', ' ян', 'яо', ' яо', 'яп', ' яп', 'яр', ' яр', 'яс', ' яс', 'яш', ' яш', 'ая', ' ая', 'ея', ' ея', 'зя', ' зя', 'ия', ' ия', 'ля', ' ля', 'мя', ' мя', 'ня', ' ня', 'оя', ' оя', 'ья', ' ья', 'эя', ' эя', 'юя', ' юя']
['сам', ' сам', 'саб', ' саб', 'саг', ' саг', 'сад', ' сад', 'сае', ' сае', 'саз', ' саз', 'саи', ' саи', 'сай', ' сай', 'сак', ' сак', 'сал', ' сал', 'сан', ' сан', 'сап', ' сап', 'сар', ' сар', 'сат', ' сат', 'саф', ' саф', 'сах', ' сах', 'сац', ' сац', 'саш', ' саш', 'саю', ' саю', 'сая', ' сая', 'сама', ' са

['от', ' от', 'то', ' то', '-то', 'о', ' о', "о'", " о'", 'о.', ' о.', 'о2', ' о2', 'об', ' об', 'од', ' од', 'ое', ' ое', 'оз', ' оз', 'ои', ' ои', 'ой', ' ой', 'ок', ' ок', 'ол', ' ол', 'ом', ' ом', 'он', ' он', 'ор', ' ор', 'ос', ' ос', 'оу', ' оу', 'оф', ' оф', 'ох', ' ох', 'ош', ' ош', 'ою', ' ою', 'оя', ' оя', 'ото', ' ото', 'отт', ' отт', 'т', ' т', 'ат', ' ат', 'вт', ' вт', 'гт', ' гт', 'ет', ' ет', 'ит', ' ит', 'кт', ' кт', 'мт', ' мт', 'нт', ' нт', 'пт', ' пт', 'ст', ' ст', 'цт', ' цт', 'чт', ' чт', 'шт', ' шт', 'ют', ' ют', 'оат', ' оат', 'окт', ' окт', 'олт', ' олт', 'опт', ' опт', 'орт', ' орт', 'ост', ' ост', 'оят', ' оят', 'о т', ' о т', 'бот', ' бот', 'вот', ' вот', 'гот', ' гот', 'дот', ' дот', 'йот', ' йот', 'кот', ' кот', 'лот', ' лот', 'мот', ' мот', 'нот', ' нот', 'пот', ' пот', 'рот', ' рот', 'сот', ' сот', 'тот', ' тот', 'уот', ' уот', 'фот', ' фот', 'хот', ' хот', 'шот', ' шот']
['москвы', ' москвы', 'москва', ' москва', 'москве', ' москве', 'москво', ' москво',

['реже', ' реже', 'режа', ' режа', 'режу', ' режу', 'режь', ' режь', 'режем', ' режем', 'режет', ' режет', 'рее', ' рее', 'ребе', ' ребе', 'реве', ' реве', 'реге', ' реге', 'резе', ' резе', 'реке', ' реке', 'реле', ' реле', 'реме', ' реме', 'рене', ' рене', 'репе', ' репе', 'рече', ' рече', 'реше', ' реше', 'ре е', ' ре е', 'рже', ' рже', 'раже', ' раже', 'роже', ' роже', 'рыже', ' рыже', 'ряже', ' ряже', 'р же', ' р же', 'редже', ' редже', 'ре же', ' ре же', 'еже', ' еже', 'веже', ' веже', 'деже', ' деже', 'леже', ' леже', 'меже', ' меже', 'сеже', ' сеже', 'р еже', ' р еже', 'вреже', ' вреже', 'мреже', ' мреже']
['вроде', 'ворде', 'вреде', 'воде', 'вводе', 'виоде', 'входе', 'в оде', 'роде', 'броде', 'ироде', 'уроде', 'юроде', 'в роде']
['прокапало', ' прокапало', 'прокатало', ' прокатало', 'прокачало', ' прокачало', 'прока ало', ' прока ало', 'прок нало', ' прок нало', 'прока нало', ' прока нало', 'пр канало', ' пр канало', 'про канало', ' про канало', 'проканало', ' проканало']
['но'

['эта', ' эта', 'эти', ' эти', 'это', ' это', 'этт', ' этт', 'эту', ' эту', 'этаж', ' этаж', 'этак', ' этак', 'этан', ' этан', 'этап', ' этап', 'эва', ' эва', 'эда', ' эда', 'эка', ' эка', 'эла', ' эла', 'эма', ' эма', 'эра', ' эра', 'эфа', ' эфа', 'эха', ' эха', 'эша', ' эша', 'этна', ' этна', 'этта', ' этта', 'та', ' та', 'ата', ' ата', 'ета', ' ета', 'рта', ' рта', 'ста', ' ста', 'юта', ' юта', 'эрта', ' эрта', 'эста', ' эста', 'бэта', ' бэта', 'мэта', ' мэта', 'нэта', ' нэта', 'пэта', ' пэта', 'тэта', ' тэта']
['колонка', ' колонка', 'колонке', ' колонке', 'колонки', ' колонки', 'колонко', ' колонко', 'колонку', ' колонку', 'колонкам', ' колонкам', 'колонках', ' колонках', 'колона', ' колона', 'колонна', ' колонна', 'колон а', ' колон а', 'колобка', ' колобка', 'колодка', ' колодка', 'колоска', ' колоска', 'коло ка', ' коло ка', 'колон ка', ' колон ка', 'коленка', ' коленка', 'козонка', ' козонка', 'коронка', ' коронка', 'болонка', ' болонка', 'солонка', ' солонка']
['пос три', ' п

['в', ' в', '$', ' $', '%', ' %', '?', ' ?', '£', ' £', '§', ' §', '°', ' °', 'а', ' а', 'б', ' б', 'г', ' г', 'д', ' д', 'е', ' е', 'ж', ' ж', 'и', ' и', 'й', ' й', 'к', ' к', 'л', ' л', 'м', ' м', 'о', ' о', 'п', ' п', 'р', ' р', 'с', ' с', 'т', ' т', 'у', ' у', 'х', ' х', 'ц', ' ц', 'ч', ' ч', 'ш', ' ш', 'ь', ' ь', 'ю', ' ю', 'я', ' я', 'в.', ' в.', 'ва', ' ва', 'вб', ' вб', 'ве', ' ве', 'ви', ' ви', 'во', ' во', 'вс', ' вс', 'вт', ' вт', 'ву', ' ву', 'вц', ' вц', 'вы', ' вы', 'ав', ' ав', 'гв', ' гв', 'дв', ' дв', 'ев', ' ев', 'зв', ' зв', 'ив', ' ив', 'кв', ' кв', 'мв', ' мв', 'нв', ' нв', 'св', ' св', 'тв', ' тв', 'эв', ' эв']
['это', ' это', 'эта', ' эта', 'эти', ' эти', 'этт', ' этт', 'эту', ' эту', 'этой', ' этой', 'этол', ' этол', 'этом', ' этом', 'этот', ' этот', 'этою', ' этою', 'эво', ' эво', 'эго', ' эго', 'эдо', ' эдо', 'эко', ' эко', 'эмо', ' эмо', 'эно', ' эно', 'эро', ' эро', 'эфо', ' эфо', 'эхо', ' эхо', 'этно', ' этно', 'то', ' то', '-то', 'ато', ' ато', 'вто', ' вт

In [ ]:
results = evaluate_spelling_corrector(erroneous_lines, golden_lines, hypotheses)
print(results['precision'])
print(results['recall'])
print(results['f_measure'])